In [7]:
import torch
import torchvision
import coremltools as ct
import sys
sys.path.append('/Users/kalugny/Code/segment-anything')
from segment_anything import sam_model_registry, SamPredictor
from segment_anything.utils.onnx import SamOnnxModel
import base64

import onnxruntime
from onnxruntime.quantization import QuantType
from onnxruntime.quantization.quantize import quantize_dynamic

In [2]:
checkpoint = "sam_vit_h_4b8939.pth"
model_type = "vit_h"

In [6]:
embedding = "..."

In [8]:
emb_data = base64.b64decode(embedding)

In [3]:
sam = sam_model_registry[model_type](checkpoint=checkpoint)

The script `segment-anything/scripts/export_onnx_model.py` can be used to export the necessary portion of SAM. Alternatively, run the following code to export an ONNX model. If you have already exported a model, set the path below and skip to the next section. Assure that the exported ONNX model aligns with the checkpoint and model type set above. This notebook expects the model was exported with the parameter `return_single_mask=True`.

In [4]:
onnx_model_path = None  # Set to use an already exported model, then skip to the next section.

In [5]:
import warnings

onnx_model_path = "sam_onnx_example.onnx"

onnx_model = SamOnnxModel(sam, return_single_mask=True)

dynamic_axes = {
    "point_coords": {1: "num_points"},
    "point_labels": {1: "num_points"},
}

embed_dim = sam.prompt_encoder.embed_dim
embed_size = sam.prompt_encoder.image_embedding_size
mask_input_size = [4 * x for x in embed_size]
dummy_inputs = {
    "image_embeddings": torch.randn(1, embed_dim, *embed_size, dtype=torch.float),
    "point_coords": torch.randint(low=0, high=1024, size=(1, 5, 2), dtype=torch.float),
    "point_labels": torch.randint(low=0, high=4, size=(1, 5), dtype=torch.float),
    "mask_input": torch.randn(1, 1, *mask_input_size, dtype=torch.float),
    "has_mask_input": torch.tensor([1], dtype=torch.float),
    "orig_im_size": torch.tensor([1500, 2250], dtype=torch.float),
}
output_names = ["masks", "iou_predictions", "low_res_masks"]

with warnings.catch_warnings():
    warnings.filterwarnings("ignore", category=torch.jit.TracerWarning)
    warnings.filterwarnings("ignore", category=UserWarning)
    with open(onnx_model_path, "wb") as f:
        torch.onnx.export(
            onnx_model,
            tuple(dummy_inputs.values()),
            f,
            export_params=True,
            verbose=False,
            opset_version=17,
            do_constant_folding=True,
            input_names=list(dummy_inputs.keys()),
            output_names=output_names,
            dynamic_axes=dynamic_axes,
        )    

================ Diagnostic Run torch.onnx.export version 2.0.0 ================
verbose: False, log level: Level.ERROR
======================= 0 NONE 0 NOTE 0 WARNING 0 ERROR ========================



RuntimeError: The size of tensor a (1048576) must match the size of tensor b (64) at non-singleton dimension 3

If desired, the model can additionally be quantized and optimized. We find this improves web runtime significantly for negligible change in qualitative performance. Run the next cell to quantize the model, or skip to the next section otherwise.

In [ ]:
trace = torch.jit.trace(onnx_model.eval(), tuple(dummy_inputs.values()))

In [10]:
coreml_inputs = {
    "image_embeddings": ct.TensorType(name="image_embeddings", shape=dummy_inputs["image_embeddings"].shape),
    "point_coords": ct.TensorType(name="point_coords", shape=dummy_inputs["point_coords"].shape),
    "point_labels": ct.TensorType(name="point_labels", shape=dummy_inputs["point_labels"].shape),
    "mask_input": ct.TensorType(name="mask_input", shape=dummy_inputs["mask_input"].shape),
    "has_mask_input": ct.TensorType(name="has_mask_input", shape=dummy_inputs["has_mask_input"].shape),
    "orig_im_size": ct.TensorType(name="orig_im_size", shape=dummy_inputs["orig_im_size"].shape),
}


In [18]:
model = ct.convert(
        trace,
        inputs=list(coreml_inputs.values()),
        minimum_deployment_target=ct.target.macOS13
    )

Converting PyTorch Frontend ==> MIL Ops:  20%|█████████████████████████▏                                                                                                    | 185/924 [00:00<00:00, 7065.68 ops/s]


RuntimeError: PyTorch convert function for op 'repeat_interleave' not implemented.